In [1]:
from tqdm import tqdm
import pandas as pd
import numpy as np
import scipy
import sys
sys.path.append("..")
import os
pd.set_option("max_columns", 10000)

%pylab inline
import seaborn as sns

import warnings
warnings.filterwarnings('ignore')

import json
from IPython import display

from tqdm import tqdm, tqdm_notebook, tqdm_pandas
tqdm.pandas()

import copy

from Scripts.saving import submit

from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

from Scripts.utils import *

import json

import featuretools as ft

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode(connected=True)

Populating the interactive namespace from numpy and matplotlib


In [2]:
base_dir = ".."
input_dir = open( os.path.join(base_dir, "datadir.txt"), "r").read()[:-1]
pred_dir = os.path.join(base_dir, "predictions")
processed_dir = os.path.join(input_dir, "processed")
!tree {input_dir}

/media/furfa/Data/Datasets/ai-academy2019/input [error opening dir]

0 directories, 0 files


In [3]:
y_train = pd.read_csv( os.path.join(input_dir,"processed", 'train_all_JSON.csv'), index_col=0 ).skilled

In [4]:
train = pd.read_csv(
    os.path.join(processed_dir, "train_df_0.814.csv"), index_col=0
)
test = pd.read_csv(
    os.path.join(processed_dir, "test_df_0.814.csv"), index_col=0
)

In [5]:
train = pd.concat([
    train, 
    pd.read_csv(
        os.path.join(processed_dir, "train_timeseries_no_zeros.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "train_ability_upgrades.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "train_damage_targets.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "train_team.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "train_item_purchase_log.csv"), index_col=0
    ),
    
],axis = 1)
train.drop(
            [c for c in train.columns if c.endswith("mode")],
            axis=1,
            inplace=True
)

In [6]:
test = pd.concat([
    test, 
    pd.read_csv(
        os.path.join(processed_dir, "test_timeseries_no_zeros.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "test_ability_upgrades.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "test_damage_targets.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "test_team.csv"), index_col=0
    ),
    pd.read_csv(
        os.path.join(processed_dir, "test_item_purchase_log.csv"), index_col=0
    ),
    
],axis = 1)
test.drop(
            [c for c in test.columns if c.endswith("mode")],
            axis=1,
            inplace=True
)

In [7]:
in_train_and_test = list(
    set(train.columns).intersection( set(test.columns) )
)
train = train[in_train_and_test]
test = test[in_train_and_test]

In [8]:
all( test.columns == train.columns )

True

In [12]:
train.shape

(99871, 1450)

In [13]:
train.sample()

rune_pickups  sentry_wards_placed  first_buy_time_18  \
5068             4                   10                  0   

      npc_dota_visage_familiar1  player->0_var  player->0_var  \
5068                          0     18123052.0   1.812305e+07   

      dire->1_var * radiant->3_std  first_buy_time_254  \
5068                    18762368.0                   0   

      best_xpm_x16 * farm_score  radiant->1_linreg_trend / radiant->0_skew  \
5068                    78765.0                                   0.865723   

      first_buy_time_173  count_item_76  fight_score  \
5068                   0              0        0.636   

      avg_gpm_x16 / avg_kills_x16  avg_kills_x16 * avg_xpm_x16  \
5068                        93.25                         1800   

      count_item_248  count_item_1025  npc_dota_pugna_nether_ward_3  \
5068               0                0                             0   

      npc_dota_juggernaut_healing_ward  avg_assists_x16 * avg_xpm_x16  \
5068                                 0                           7200   

      player->1_skew * radiant->0_skew  npc_dota_hero_dazzle  count_item_85  \
5068                          1.297852                     0              0   

      first_buy_time_257  dire2  pre_game_duration / avg_xpm_x16  \
5068                 806     36                              0.2   

      player->3_var  player->3_var  \
5068       9713.591     9713.59034   

      npc_dota_creep_badguys_melee_upgraded_mega  \
5068                                           0   

      dire->0_linreg_trend * radiant->0_linreg_trend  \
5068                                         29152.0   

      npc_dota_warlock_golem_scepter_1  npc_dota_lesser_eidolon  \
5068                                 0                        0   

      count_item_50  avg_gpm_x16 * best_kills_x16  \
5068              0                          4476   

      npc_dota_neutral_kobold_tunneler  npc_dota_neutral_centaur_khan  \
5068                                 0                           2200   

      radiant->0_sum  radiant->0_sum  radiant->1_var / dire->1_var  \
5068        19216950        19216950                      0.480617   

      avg_kills_x16 * best_kills_x16  dire->1_linreg_trend * radiant->1_mean  \
5068                              48                                 82.6875   

      count_item_56  time->3_var  time->3_var  duration / best_assists_x16  \
5068              1     0.000447     0.000447                    70.605263   

      fin_item_9  npc_dota_hero_lich  time->0_amax / radiant->0_std  \
5068           0                   0                        0.10878   

      player->1_var  player->1_var  count_item_268  npc_dota_hero_bloodseeker  \
5068      2916.0757    2916.075565               0                          0   

      npc_dota_hero_monkey_king  hero_pick_order * level  \
5068                          0                       40   

      best_assists_x16 * pre_game_duration  dire->0_amax * dire->0_skew  \
5068                                  3420                 50099.431641   

      best_assists_x16 * last_hits  count_item_14  \
5068                          1862              0   

      time->3_sum / radiant->1_mean  count_item_88  npc_dota_lycan_wolf1  \
5068                       57.59375              0                     0   

      assists * net_worth  count_item_78  npc_dota_hero_pudge  count_item_157  \
5068               102396              0                    0               0   

      best_assists_x16 * best_kills_x16  avg_assists_x16  \
5068                                456               16   

      npc_dota_goodguys_range_rax_mid  npc_dota_hero_treant  \
5068                                0                     0   

      first_buy_time_202  avg_deaths_x16 * xp_per_min  first_blood_claimed  \
5068                   0                         3528                    0   

      npc_dota_creep_badguys_ranged  \
5068                           4148   

      npc_dota_c

In [ ]:
from sklearn.model_selection import cross_val_score
import catboost as cb

score = cross_val_score(
    cb.CatBoostClassifier(logging_level="Silent"),
    train,
    y_train,
    scoring="accuracy",
    cv = 4,
    verbose=0,
    n_jobs=-1
)
print(score, np.mean(score), np.std(score))

In [13]:
# На обновленном кэтбусте
from sklearn.model_selection import cross_val_score
import catboost as cb

score = cross_val_score(
    cb.CatBoostClassifier(logging_level="Silent"),
    train,
    y_train,
    scoring="accuracy",
    cv = 4,
    verbose=0,
    n_jobs=-1
)
print(score, np.mean(score), np.std(score))

[0.83439465 0.83590996 0.83362038 0.83498218] 0.8347267923732978 0.0008365984213307685


In [12]:
model = cb.CatBoostClassifier().fit(
    train, 
    y_train)

y_pred = model.predict(
    test
)

y_pred = pd.DataFrame({'id' : test.index, 'skilled': y_pred})
submit(y_pred, "top_df_raw")

Learning rate set to 0.061655
0:	learn: 0.6765500	total: 214ms	remaining: 3m 33s
1:	learn: 0.6620110	total: 376ms	remaining: 3m 7s
2:	learn: 0.6491235	total: 539ms	remaining: 2m 59s
3:	learn: 0.6375100	total: 702ms	remaining: 2m 54s
4:	learn: 0.6270728	total: 864ms	remaining: 2m 51s
5:	learn: 0.6173941	total: 1.03s	remaining: 2m 50s
6:	learn: 0.6091016	total: 1.19s	remaining: 2m 49s
7:	learn: 0.6008819	total: 1.35s	remaining: 2m 47s
8:	learn: 0.5941807	total: 1.51s	remaining: 2m 46s
9:	learn: 0.5873047	total: 1.68s	remaining: 2m 46s
10:	learn: 0.5810860	total: 1.86s	remaining: 2m 47s
11:	learn: 0.5756950	total: 2.03s	remaining: 2m 47s
12:	learn: 0.5694842	total: 2.19s	remaining: 2m 46s
13:	learn: 0.5646851	total: 2.36s	remaining: 2m 46s
14:	learn: 0.5601684	total: 2.52s	remaining: 2m 45s
15:	learn: 0.5561251	total: 2.69s	remaining: 2m 45s
16:	learn: 0.5512818	total: 2.85s	remaining: 2m 44s
17:	learn: 0.5471347	total: 3.02s	remaining: 2m 44s
18:	learn: 0.5428742	total: 3.19s	remaining: 

# Кластеризация по коммандам
# Аутлиеры!!!

In [12]:
y_pred.shape

(43265, 2)

In [11]:
model = cb.CatBoostClassifier(iterations=60000, logging_level='Verbose').fit(
    train, 
    y_train)

y_pred = model.predict(
    test
)

y_pred = pd.DataFrame({'id' : test.index, 'skilled': y_pred})
submit(y_pred, "top_df_cb60000")

Learning rate set to 0.001606
0:	learn: 0.6927057	total: 214ms	remaining: 3h 33m 43s
1:	learn: 0.6922971	total: 367ms	remaining: 3h 3m 31s
2:	learn: 0.6918560	total: 520ms	remaining: 2h 53m 28s
3:	learn: 0.6914214	total: 678ms	remaining: 2h 49m 24s
4:	learn: 0.6909853	total: 834ms	remaining: 2h 46m 44s
5:	learn: 0.6905470	total: 988ms	remaining: 2h 44m 35s
6:	learn: 0.6901137	total: 1.14s	remaining: 2h 43m 12s
7:	learn: 0.6896914	total: 1.29s	remaining: 2h 41m 44s
8:	learn: 0.6892730	total: 1.44s	remaining: 2h 40m 5s
9:	learn: 0.6888511	total: 1.59s	remaining: 2h 39m 30s
10:	learn: 0.6884236	total: 1.75s	remaining: 2h 39m 12s
11:	learn: 0.6879987	total: 1.91s	remaining: 2h 38m 55s
12:	learn: 0.6875855	total: 2.06s	remaining: 2h 38m 43s
13:	learn: 0.6871668	total: 2.21s	remaining: 2h 38m 8s
14:	learn: 0.6867596	total: 2.37s	remaining: 2h 37m 46s
15:	learn: 0.6863562	total: 2.51s	remaining: 2h 37m 2s
16:	learn: 0.6859360	total: 2.66s	remaining: 2h 36m 39s
17:	learn: 0.6855296	total: 2.82

In [78]:
model = cb.CatBoostClassifier(iterations=50000).fit(
    train[cols], 
    y_train)

y_pred = model.predict(
    test[cols]
)

y_pred = pd.DataFrame({'id' : test.index, 'skilled': y_pred})
submit(y_pred, "top_df_cb50000")

Learning rate set to 0.001889
0:	learn: 0.6926385	total: 71ms	remaining: 59m 10s
1:	learn: 0.6921298	total: 141ms	remaining: 58m 45s
2:	learn: 0.6916095	total: 212ms	remaining: 58m 52s
3:	learn: 0.6910972	total: 283ms	remaining: 58m 51s
4:	learn: 0.6905804	total: 353ms	remaining: 58m 51s
5:	learn: 0.6900834	total: 424ms	remaining: 58m 52s
6:	learn: 0.6895903	total: 494ms	remaining: 58m 50s
7:	learn: 0.6890814	total: 566ms	remaining: 58m 55s
8:	learn: 0.6885744	total: 637ms	remaining: 58m 56s
9:	learn: 0.6880816	total: 707ms	remaining: 58m 56s
10:	learn: 0.6876197	total: 779ms	remaining: 58m 59s
11:	learn: 0.6871164	total: 850ms	remaining: 58m 59s
12:	learn: 0.6866269	total: 922ms	remaining: 59m 4s
13:	learn: 0.6861294	total: 993ms	remaining: 59m 5s
14:	learn: 0.6856354	total: 1.06s	remaining: 59m 6s
15:	learn: 0.6851539	total: 1.13s	remaining: 59m 5s
16:	learn: 0.6846723	total: 1.21s	remaining: 59m 4s
17:	learn: 0.6841983	total: 1.27s	remaining: 59m 2s
18:	learn: 0.6837238	total: 1.35s

In [41]:
# aditional
abilities = pd.read_csv( os.path.join(input_dir, 'dota2_abilities.csv') ).drop(["dname", "desc"], axis=1)
items = pd.read_csv( os.path.join(input_dir,"processed", 'items_proc.csv') )
heroes = pd.read_csv( 
    os.path.join(input_dir,"processed", 'heroes_proc.csv') 
).set_index("hero_id").drop('Unnamed: 0', axis=1)

In [64]:
x = "dire"
[c for c in train.columns if re.match(rf"{x}\d", c)]

['dire1', 'dire2', 'dire3', 'dire4', 'dire5']

In [73]:
def process_heroes(df, prefix):
    col_selection = [c for c in df.columns if re.match(rf"{prefix}\d", c)]
    
    sel_val = train[col_selection].values
    new_df = pd.concat(
                [
                    heroes.ix[ sel_val[i] ].sum()
                        for i in tqdm(range(df.shape[0]))
                ], axis=1
            )
    ret = new_df.T.add_prefix(prefix+"_")
    ret.index = df.index
    return ret

In [74]:
new_train = pd.concat(
    (
        train,
        process_heroes(train, "dire"),
        process_heroes(train, "radiant"),
    ), axis=1
)

100%|██████████| 99871/99871 [01:08<00:00, 1464.92it/s]


In [76]:
new_test = pd.concat(
    (
        test,
        process_heroes(test, "dire"),
        process_heroes(test, "radiant"),
    ), axis=1
)

100%|██████████| 43265/43265 [00:30<00:00, 1432.58it/s]


In [75]:
from sklearn.model_selection import cross_val_score
import catboost as cb

score = cross_val_score(
    cb.CatBoostClassifier(logging_level="Silent"),
    new_train,
    y_train,
    scoring="accuracy",
    cv = 4,
    verbose=0,
    n_jobs=-1
)
print(score, np.mean(score), np.std(score))

Learning rate set to 0.056834
Learning rate set to 0.056834
Learning rate set to 0.056834
Learning rate set to 0.056834
[0.81816725 0.82016982 0.819529   0.82056314] 0.8196073029792469 0.000909660084010261


## Написать генератор дифов

In [11]:
model = cb.CatBoostClassifier(iterations=100000).fit(
    new_train, 
    y_train)

y_pred = model.predict(
    new_test
)

y_pred = pd.DataFrame({'id' : test.index, 'skilled': y_pred})
submit(y_pred, "top_df+team_cb100000")

NameError: name 'new_train' is not defined